# packing

In [1]:
import tvm
from tvm.relax.frontend import nn
from tvm.script import ir as I
from tvm.script import relax as R

def _iter_binding_names(mod):
    """Helper function to compare the names of relax variables"""
    for block in mod["forward"].body.blocks:
        for binding in block.bindings:
            yield binding.var.name_hint

In [2]:
class TestModule(nn.Module):
    def __init__(self, in_features: int, out_features: int):
        super().__init__()
        self.in_features = in_features
        self.out_features = out_features
        self.linear_1 = nn.Linear(in_features, out_features, bias=False)
        self.linear_2 = nn.Linear(in_features, out_features, bias=False)

    def forward(self, x: nn.Tensor):
        x1 = self.linear_1(x)
        x2 = self.linear_2(x)
        return x1 + x2

model = TestModule(10, 20)
mod, _ = model.export_tvm(
    spec={
        "forward": {
            "x": nn.spec.Tensor([1, model.in_features], "float32"),
            "$": {
                "param_mode": "packed",
                "effect_mode": "none",
            },
        }
    }
)
mod.show()